### Purpose of this file ###
The file B2356run2.mat holds the transient info for the tire run that we care about. 

In this file, we try to synthesize the following : 
- Tire Temp versus Time
- $\mu (x)$ and $\mu (y)$ versus temp
- The value L (relaxation length -- distance traveled to hit 67.2% of total distance)

In [2]:
import numpy as np 
import scipy
from scipy.io import loadmat
import matplotlib.pyplot as plt 
import pandas as pd 

In [3]:
mat = loadmat('B2356run2.mat')
mat = {k:v for k, v in mat.items() if k not in {'__header__', '__version__', '__globals__', 'channel', 'source', 'testid', 'tireid'}}

# each column is of shape (58755, 1). Need to squeeze into 1D
mat = {k:v.squeeze() for k,v in mat.items()}
df = pd.DataFrame(mat)
# sort values in order of increasing time
df = df.sort_values(by='ET')
df.shape
df.head()

AMBTMP    ET    FX     FY      FZ     IA    MX    MZ     N     NFX  ...  \
0   25.55  0.16  2.10 -28.53 -662.39 -0.005 -5.48  0.98  0.03 -0.0032  ...   
1   25.55  0.17  3.05 -28.05 -665.15  0.013 -4.50  1.42 -0.04 -0.0046  ...   
2   25.57  0.18  1.83 -29.31 -661.93  0.001 -6.25  0.85  0.03 -0.0028  ...   
3   25.56  0.19  1.83 -29.24 -661.79 -0.005 -6.04  0.82  0.09 -0.0028  ...   
4   25.55  0.20  2.11 -30.81 -663.24  0.010 -6.20  1.06  0.03 -0.0032  ...   

      RL    RST  RUN     SA   SL      SR   TSTC   TSTI   TSTO     V  
0  19.54  26.97    2 -0.003 -0.0 -0.6365  26.25  26.29  27.29  0.01  
1  19.53  27.00    2 -0.004 -0.0 -1.0932  26.25  26.30  27.25  0.03  
2  19.53  27.00    2  0.006 -0.0 -0.9547  26.23  26.35  27.25  0.04  
3  19.54  27.02    2  0.002 -0.0 -0.7908  26.24  26.31  27.27  0.03  
4  19.53  27.04    2  0.006 -0.0 -0.9547  26.26  26.32  27.26  0.04  

[5 rows x 23 columns]

In [20]:
# Visualize tire info over time
import matplotlib.pyplot as plt
from scipy.signal import savgol_filter, butter, filtfilt

plt_per_row = 1
columns_to_plot = [col for col in df.columns if col != 'ET']

n_plots = len(list(columns_to_plot))
n_rows = int(np.ceil((n_plots) / plt_per_row))  # Arrange 3 plots per row
df_size = df.shape[0]
fig, axes = plt.subplots(n_rows, plt_per_row, figsize=(36, n_rows * 12))
axes = axes.flatten()  # Flatten the axes array for easier indexing

# Filtering - Butterworth
def butter_lowpass_filter(data, cutoff=0.01, fs=1.0, order=4):
    nyquist = 0.5 * fs
    normal_cutoff = cutoff / nyquist
    b, a = butter(order, normal_cutoff, btype='low', analog=False)
    return filtfilt(b, a, data)
filtered_df = df.apply(lambda col: butter_lowpass_filter(col) if col.name != 'ET' else col)
filtered_df['TSTC'] = butter_lowpass_filter(filtered_df['TSTC'], cutoff=0.005)
filtered_df['TSTI'] = butter_lowpass_filter(filtered_df['TSTI'], cutoff=0.005)
filtered_df['TSTO'] = butter_lowpass_filter(filtered_df['TSTO'], cutoff=0.005)
# Filtering - Savgol
# window_size = 19
# degree = 4
# filtered_df = df.apply(lambda col: savgol_filter(col, window_size, degree) if col.name != 'ET' else col)

# Plot every column w.r.t ET
for i, col in enumerate(columns_to_plot):
    ax = axes[i]
    ax.set_title(f"ET vs {col}")
    ax.set_xlabel('ET')
    ax.set_ylabel(col)
    
    # Plot raw data
    ax.plot(df['ET'], df[col], label="raw")

    # Plot filtered values
    ax.plot(filtered_df['ET'], filtered_df[col], label = "filtered")
    # Plot best-fit spline
    # spline = scipy.interpolate.make_splrep(df['ET'], df[col], s=df_size // 100)
    # l_bound, r_bound = df['ET'][0], df['ET'][df_size - 1]
    # num_pts = int(np.ceil((r_bound - l_bound))) * 100 # plot every 100th of a second
    # et_continuous = np.linspace(l_bound, r_bound, num_pts)
    # col_continuous = spline(et_continuous)
    # ax.plot(et_continuous, col_continuous, label="spline")

    ax.legend()
# Adjust layout
plt.tight_layout()
plt.show()


### From observing the above data, we know the following :  ###

We test 3 tire pressures. For each tire pressure, we test 3 slip angles. For each pressure/angle combo, we test 3 normal loads.